In [9]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [10]:
# Carga Fichero

import pandas as pd
#path="/content/drive/MyDrive/Cajamar/"
#datos = pd.read_csv(path+'Modelar_UH2022.txt',sep='|',parse_dates=['SAMPLETIME'],infer_datetime_format=True)
#datos = pd.read_csv('Modelar_UH2022.txt',sep='|',parse_dates=['SAMPLETIME'],infer_datetime_format=True)

In [11]:
#path_2="/content/drive/MyDrive/Cajamar/Temperatura/"
#datos_temp = pd.read_csv(path_2+'AVAMET_Cajamar_prueba_2.csv',sep=',',parse_dates=['Timestamp'],infer_datetime_format=True,index_col=0)
#print(datos_temp)
#print(datos_temp.dtypes)

In [12]:
!pip install skforecast

In [48]:
# Librerias

import pandas as pd
from tqdm import tqdm
from datetime import timedelta
from datetime import date
from sklearn.metrics import mean_squared_error
import matplotlib.pyplot as plt
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import ExtraTreesRegressor
from skforecast.ForecasterAutoreg import ForecasterAutoreg
from skforecast.model_selection import grid_search_forecaster
from sklearn.preprocessing import StandardScaler
import math
from joblib import dump, load
import numpy as np


class Contador(object):
    def __init__(self, datos_contador, ID, umbral,datos_temp):
        self.datos_contador = datos_contador
        self.ID = ID
        self.umbral = umbral
        self.datos_temp=datos_temp
        self.Preprocesado()
        self.SinDatos = False  # NO TIENE DATOS DATASET VACIO
        #self.outlier = False
        self.dias = 0
        self.RMSE_Train = 0
        self.RMSE_Test = 0
        self.datos_test = pd.DataFrame()
        self.Mejor_Parametro = {}
        self.Mejor_Lag = 14 
        
        # {'ID','Dia_1':0,'Dia_2':0,'Dia_3':0,'Dia_4':0,'Dia_5':0,'Dia_6':0','Dia_7':0,'Semana_1':0,'Semana_2':0}
        self.Predicciones = [self.ID,0,0,0,0,0,0,0,0,0]
        
        if not datos_contador.empty:
            # CALCULO LECTURA CONTADOR Y CONSUMO JUNTANDO DECIMALES
            #
            
            self.datos_contador = self.datos_contador.set_index('SAMPLETIME')
            self.datos_contador['CONSUMO'] = self.datos_contador['DELTAINTEGER'] + (self.datos_contador['DELTATHOUSANDTH'] / 100)
            self.datos_contador['LECTURA'] = self.datos_contador['READINGINTEGER'] + (self.datos_contador['READINGTHOUSANDTH'] / 100)

            # CONSUMO POR DIAS
            # RESAMPLE
            # Tmin       Temp       Tmax    Humedad Precip

            self.datos_consumo = pd.DataFrame(self.datos_contador.resample(rule='1D', closed='left', label ='left').sum())
            print(len(self.datos_temp))
            while 365>len(self.datos_consumo):
                      self.datos_consumo = self.datos_consumo.append([0,0,0,0], ignore_index = True)
                      print(len(self.datos_consumo))

            while 365<len(self.datos_consumo):
                      self.datos_consumo = self.datos_consumo.iloc[1: , :]
                      print(len(self.datos_consumo))
                      

            index = pd.date_range('2019-02-01', '2020-01-31')
            self.datos_consumo = self.datos_consumo.set_index(index)
            self.datos_consumo.fillna(0,inplace=True)

            self.datos_temp = self.datos_temp.set_index(self.datos_consumo.index)
            self.datos_consumo["Temp"]=self.datos_temp["Temp"]
            self.datos_consumo["Tmin"]=self.datos_temp["Tmin"]
            self.datos_consumo["Tmax"]=self.datos_temp["Tmax"]
            self.datos_consumo["Humedad"]=self.datos_temp["Humedad"]
            self.datos_consumo["Precip"]=self.datos_temp["Precip"]



            #print(self.datos_consumo)
            self.datos_consumo['CONSUMO_NORM'] = (self.datos_consumo['CONSUMO'] - self.datos_consumo['CONSUMO'].mean()) / self.datos_consumo['CONSUMO'].std()
            # COGER SOLO SEMANAS COMPLETAS
            
            self.datos_consumo_semanal = pd.DataFrame(self.datos_contador.resample(rule='1W', closed='left', label ='left',offset='-36h').sum())

            # ESTADISTICAS
            #self.dias = len(self.datos_consumo.index)
            self.dias = (self.datos_contador['CONSUMO'] > 0).sum()  ####################

            #self.datos_consumo['Cuenta'] = self.datos_contador.groupby([self.datos_contador.index.year,self.datos_contador.index.month, self.datos_contador.index.day]).agg({'CONSUMO':'count'}).values
            
            
            self.fecha_inicio_contador= self.datos_consumo.index[0]
            self.fecha_fin_contador= self.datos_consumo.index[-1]
            
        else:
            self.datos_consumo = pd.DataFrame()
            self.SinDatos = True
            self.fecha_fin_contador = None

        # GENERACION DEL MODELO
        self.modelo()
    
    def __Convertir_fecha(self, serie):
        fechas = []
        for año, mes, dia in serie.index:
            fechas.append(date(año,mes,dia))
        return fechas
    
    def Preprocesado(self):
        # SAMPLETIME READINGINTEGER	READINGTHOUSANDTH	DELTAINTEGER	DELTATHOUSANDTH
        # VALORES  NULOS 
        # VALORES ENTEROS INTERPOLAMOS
        

        self.datos_contador['READINGINTEGER'].interpolate(inplace=True)
        self.datos_contador['DELTAINTEGER'].interpolate(inplace=True)
        
        # VALORES DECIMALES SUSTITUIMOS POR CERO
        self.datos_contador['READINGTHOUSANDTH'].fillna(0,inplace=True)
        self.datos_contador['DELTATHOUSANDTH'].fillna(0,inplace=True)
        
        # ELIMINAR VALORES NEGATIVOS
        indices = self.datos_contador[self.datos_contador['READINGINTEGER'] < 0].index
        self.datos_contador.drop(indices,inplace=True)
        indices = self.datos_contador[self.datos_contador['DELTAINTEGER'] < 0].index
        self.datos_contador.drop(indices,inplace=True)

        # NORMALIZAR

    def modelo(self):
        # DECISION DEL MODELO A TOMAR EN FUNCION DE LA ESTADISTICAS
        # CARGA DEL MODELO
        # PACO
        self.model = None
        if self.dias > self.umbral: 
            if self.fecha_fin_contador == date(2020,1,31):
                # RandomForestRegressor Diario
                self.model = ForecasterAutoreg(regressor=RandomForestRegressor(random_state=123), lags=14)
                # RandomForestRegressor Semanal Paco
                self.model_Semanal = ForecasterAutoreg(regressor=RandomForestRegressor(random_state=123), lags=14)
                
            else:
                self.model = self.datos_consumo['CONSUMO'].mean()
        else:
            if self.dias > 0: 
                #if (self.fecha_fin_contador > date(2020,1,17)).bool() :    # HACE MEDIA SI TENEMOS DATOS EN LOS ULTIMOS 14 DIAS
                self.model = self.datos_consumo['CONSUMO'].mean()
                #else:
                #self.model = 0
            else:
                self.model = 0

    def Juntar_Datos(self):
        # REHACE EL MODELO CON LOS MEJORES PARAMETROS
        # JUNTA TODO EN datos_consumo
        # {'max_depth': 3, 'n_estimators': 200}        
        #del self.model
        #if self.dias > umbral:
            #self.model = ForecasterAutoreg(regressor=RandomForestRegressor(random_state=123), lags=max(self.Mejor_Lag), 
            #                                max_depth=self.Mejor_Parametro['max_depth'],n_estimators=self.Mejor_Parametro['n_estimators'])

        self.datos_consumo = pd.concat([self.datos_consumo,self.datos_test])
        self.datos_test =pd.DataFrame()
        
    

class CajaMar_Water(object):
    def __init__(self,Ruta_Datos, Fecha_Inicio=date(2019,2,1),Fecha_Fin=date(2020,1,31),umbral_modelo=100):
        self.Ruta_Datos = Ruta_Datos
        path_2="/content/drive/MyDrive/Cajamar/Temperatura/"
        self.datos_temp = pd.read_csv(path_2+'AVAMET_Cajamar_prueba_2.csv',sep=',',parse_dates=['Timestamp'],infer_datetime_format=True,index_col=0)
        self.Fecha_Inicio = Fecha_Inicio
        self.Fecha_Fin = Fecha_Fin
        self.umbral_modelo = umbral_modelo
        self.datos = pd.DataFrame()
        self.contadores = []
        self.dias_test = 14     # DIAS QUE SE RESERVAN PARA TEST EMPEZANDO POR LA FECHA MAS RECIENTE
        self.Cargar_Datos()
        self.RMSE_Test_Promedio=0
        self.RMSE_Test_Suma=0
    

    def Cargar_Datos(self):
        print('CARGANDO DATOS.....')
        self.datos = pd.read_csv(self.Ruta_Datos,sep='|',parse_dates=['SAMPLETIME'],infer_datetime_format=True,encoding='utf-8')
        self.datos.sort_values(by=['ID','SAMPLETIME'],inplace=True)
 
        # GENERANDO CONTADORES
        print('GENERANDO CONTADORES.....')
        for ID in tqdm(pd.unique(self.datos['ID'])):
            # ALMACENAMOS ID DE CONTADOR Y BORRAMOS LA COLUMNA
            self.contadores.append(Contador(self.datos[self.datos['ID']==ID].drop('ID',axis=1),ID,self.umbral_modelo,self.datos_temp))

        print('PROCESO DE CARGA FINALIZADO')
    
    def PartirDatos(self):
        # Separar datos de entrenamiento y test / validacion (dias=0 no hace validacion)
        if self.dias_test > 0:     
            for contador in tqdm(self.contadores):
                if contador.SinDatos == False:      # COMPROBAMOS QUE HAY ALGUN REGISTRO
                    #if (contador.fecha_fin_contador==self.Fecha_Fin):
                    if contador.dias > self.dias_test + 1:    # COMPROBAMOS QUE HAY SUFICIENTES DATOS PARA HACER PARTICION
                        contador.datos_test = contador.datos_consumo.tail(self.dias_test)
                        contador.datos_consumo = contador.datos_consumo[0:-self.dias_test]


    def Grid_Search(self,ID,steps):
        # Hiperparámetros del regresor
        param_grid = {'n_estimators': [100],
              'max_depth': [5]}

        # Lags utilizados como predictores
        lags_grid = [14]

        resultados_grid = grid_search_forecaster(
                                forecaster         = self.contadores[ID].model,
                                y                  = self.contadores[ID].datos_consumo['CONSUMO'],
                                param_grid         = param_grid,
                                lags_grid          = lags_grid,
                                steps              = steps,
                                refit              = True,
                                metric             = 'mean_squared_error',
                                initial_train_size = int(len(self.contadores[ID].datos_consumo)*0.8),
                                return_best        = True,
                                verbose            = False)
        self.contadores[ID].RMSE_Train = math.sqrt(resultados_grid['metric'].head(1))
        self.contadores[ID].Mejor_Parametro = list(resultados_grid['params'])[0]
        self.contadores[ID].Mejor_Lag = max(list(resultados_grid['lags'].head(1))[0])
        

    def Entrenamiento(self,Grid=False):
        # Entrenamiento de los modelos en self.contadores(lista) 
        # iterar lista y llamar a self.contadores[iter].modelo.train
        # Rellena la variable self.contadores.Predicciones
        indexC = 0
        for contador in tqdm(self.contadores):
            if isinstance(contador.model,ForecasterAutoreg):    # COMPROBAMOS QUE ES UN MODELO
                if Grid:
                    self.Grid_Search(indexC,self.dias_test)
                    #contador.Juntar_Datos() #  JUNTA LOS DATOS PARA LUEGO HACER PREDICT
                #Tmin       Temp       Tmax    Humedad Precip
                #contador.model.fit(y=contador.datos_consumo['CONSUMO_NORM'])
                contador.model.fit(y=contador.datos_consumo['CONSUMO'],exog =contador.datos_consumo[["Temp","Tmin","Tmax","Humedad","Precip"]])
                # HAY QUE TENER EN CUENTA CUANDO TERMINAN LOS DATOS
                #predict = contador.model.predict(steps=self.dias_test) * contador.datos_consumo['CONSUMO'].std() + contador.datos_consumo['CONSUMO'].mean()
                predict = contador.model.predict(steps=self.dias_test, exog=contador.datos_consumo[['Temp',"Tmin","Tmax","Humedad","Precip"]].tail(self.dias_test))
                index = 1
                for predict_dia in predict[0:7]:    # GUARDA 7 DIAS PREDICCION
                    contador.Predicciones[index] = predict_dia
                    index += 1
                contador.Predicciones[8]=predict[0:7].sum()     # GUARDA SEMANA1 PREDICCION
                contador.Predicciones[9]=predict[7:14].sum()    # GUARDA SEMANA2 PREDICCION
            else:
              for index in range(1,8):
                    contador.Predicciones[index] = contador.model  # GUARDAMOS MEDIA EN LOS 7 DIAS
              contador.Predicciones[8]=contador.model*7     # GUARDAMOS MEDIA SEMANA1
              contador.Predicciones[9]=contador.model*7     # GUARDAMOS MEDIA SEMANA2
            
            indexC += 1
                  

    def Calculo_RMSE(self):
        # Calculo rmse utlizando datos de test
        RMSE_Todos = []
        for contador in tqdm(self.contadores):
            #if contador.dias > 180 and len(contador.datos_test) == self.dias_test:  # VER LIMITE NO DEPENDE DE LA CLASE CONTADOR
            if len(contador.datos_test) == self.dias_test:
                media_RMSE_semanal=math.sqrt(mean_squared_error([contador.datos_test['CONSUMO'][0:7].sum(), contador.datos_test['CONSUMO'][7:14].sum()] , [contador.Predicciones[8], contador.Predicciones[9]]))
                contador.RMSE_Test = 0.5*math.sqrt(mean_squared_error(contador.datos_test['CONSUMO'][0:7],contador.Predicciones[1:8]))+0.5*media_RMSE_semanal
                # Sin raiz
                #media_RMSE_semanal=mean_squared_error([contador.datos_test['CONSUMO'][0:7].sum(), contador.datos_test['CONSUMO'][7:14].sum()] , [contador.Predicciones[8], contador.Predicciones[9]])
                #contador.RMSE_Test = 0.5+mean_squared_error(contador.datos_test['CONSUMO'][0:7],contador.Predicciones[1:8])+0.5*media_RMSE_semanal
                RMSE_Todos.append(contador.RMSE_Test)

        self.RMSE_Test_Suma = sum(RMSE_Todos)
        self.RMSE_Test_Promedio = self.RMSE_Test_Suma / len(RMSE_Todos) 
        
    
    def GenerarResultados(self,equipo='Team2021IA3',numeral=1):
        # Mediante los datos predicciones generamos txt con el formato del datathon
        # Separando campos con “|”, el valor de la predicción en litros, y los decimales con “.” 2 decimales
        # Fichero: "Cajamar_Universitat de València (UV)_Team2021IA3_numeral.txt"
        
        columnas = ['ID','Dia_1','Dia_2','Dia_3','Dia_4','Dia_5','Dia_6','Dia_7','Semana_1','Semana_2']
        datos = []

        for contador in tqdm(self.contadores):
            datos.append(contador.Predicciones)
        
        print('TAMAÑO DE LOS DATOS: ', len(datos), 'x' ,len(datos[0]))
        
        dataset = pd.DataFrame(datos,columns=columnas)
        dataset.to_csv('Cajamar_Universitat de València (UV)_' + equipo + '_' + str(numeral) + '.txt',header=False ,sep='|' ,index=False ,decimal='.' ,float_format='%.2f')
         
    def GraficasEstadisticas(self,contador=0,Test=True):
        # GRÁFICAS DE CONTADORES INDIVIDUALES CON TEST Y PREDICCIONES
        if Test:
            fig, ax = plt.subplots(figsize=(10, 4))
            self.contadores[contador].datos_test['CONSUMO'].plot(ax=ax, label='Test', linewidth=1)
            pd.DataFrame(self.contadores[contador].Predicciones[1:8],index=self.contadores[contador].datos_test['CONSUMO'].index[0:7],columns=['Predicción']).plot(ax=ax, label='Prediccion', linewidth=1)
            ax.set_title('Consumo Agua. RMSE: ' + str(self.contadores[contador].RMSE_Test) + ' Contador: ' + str(contador))
            ax.legend();
        else:
            base = date(2020,2,1)
            index = [base + timedelta(days=x) for x in range(7)]
            index = pd.DataFrame(index)
            index.insert(1, 'SAMPLETIME', [base + timedelta(days=x) for x in range(7)], True)
            index['SAMPLETIME']=pd.to_datetime(index['SAMPLETIME'], format='%Y-%m-%d')
            index=index.set_index('SAMPLETIME')
            index_puro=index.drop([0],axis=1)
            index_puro['Predicción']=Proyecto.contadores[contador].Predicciones[1:8]
            #df_final=pd.DataFrame(index_puro.insert(1, 'Predicción', pd.Series(self.contadores[contador].Predicciones[1:8]), True))

            fig, ax = plt.subplots(figsize=(10, 4))
            self.contadores[contador].datos_consumo['CONSUMO'].plot(ax=ax, label='Consumo', linewidth=1)
            index_puro.plot(ax=ax, label='Predicción', linewidth=1)
            #pd.DataFrame(self.contadores[contador].Predicciones[1:8],index=index_puro,columns=['Predicción']).plot(ax=ax, label='Prediccion', linewidth=1)
            ax.set_title('Consumo Agua. RMSE: ' + str(self.contadores[contador].RMSE_Train) + ' Contador: ' + str(contador))
            ax.legend();

    def Guardar_Modelos(self,Ruta='./modelos/Modelo_ID_'):

        print('GUARDANDO MODELOS.....')
        for contador in tqdm(self.contadores):
            dump(contador.model,Ruta + str(contador.ID))

In [49]:
path="/content/drive/MyDrive/Cajamar/"
#path_2="/content/drive/MyDrive/Cajamar/Temperatura/"
#file_1=path+'Modelar_UH2022_10_Contadores.txt'
file_1=path+'Modelar_UH2022.txt'
#file_2=path_2+'AVAMET_Cajamar_prueba_2.csv'
Proyecto = CajaMar_Water(file_1)


CARGANDO DATOS.....
GENERANDO CONTADORES.....


  0%|          | 0/2747 [00:00<?, ?it/s]

365


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:131: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior.  In a future version these will be considered non-comparable.Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  0%|          | 4/2747 [00:00<02:45, 16.61it/s]

365
365
365
365


...

181
185
189
193
197
201
205
209
213
217
221
225
229
233
237
241
245
249
253
257
261
265
269
273
277
281
285
289
293
297
301
305
309
313
317
321
325
329
333
337
341
345
349
353
357
361
365
365
71
75
79
83
87
91
95
99
103
107
111
115
119
123
127
131
135
139
143
147
151
155
159
163
167
171
175
179
183
187
191
195
199
203
207
211
215
219
223
227
231
235
239
243
247
251
255
259
263
267
271
275
279
283
287
291
295
299
303
307
311
315
319
323
327
331
335
339
343
347
351
355
359
363
367
366
365


100%|█████████▉| 2746/2747 [03:53<00:00,  3.45it/s]

365
5
9
13
17
21
25
29
33
37
41
45
49
53
57
61
65
69
73
77
81
85
89
93
97
101
105
109
113
117
121
125
129
133
137
141
145
149
153
157
161
165
169
173
177
181
185
189
193
197
201
205
209
213
217
221
225
229
233
237
241
245
249
253
257
261
265
269
273
277
281
285
289
293


100%|██████████| 2747/2747 [03:54<00:00, 11.73it/s]

297
301
305
309
313
317
321
325
329
333
337
341
345
349
353
357
361
365
PROCESO DE CARGA FINALIZADO


In [50]:
#Proyecto = CajaMar_Water('Modelar_UH2022.txt')
Proyecto.PartirDatos()
Proyecto.Entrenamiento(Grid=True)
Proyecto.Calculo_RMSE()
# RELLENADO RMSE_Train y RMSE_Test y model con el mejor modelo
# VOLVEMOS A JUNTAR LOS 14 DIAS
for contador in Proyecto.contadores:
    contador.Juntar_Datos()
Proyecto.Entrenamiento()
Proyecto.GenerarResultados(equipo='GRID')


  0%|          | 0/2747 [00:00<?, ?it/s]

Number of models compared: 1


loop lags_grid: 100%|███████████████████████████████████████| 1/1 [00:02<00:00,  2.26s/it]


`Forecaster` refitted using the best-found lags and parameters, and the whole data set: 
  Lags: [ 1  2  3  4  5  6  7  8  9 10 11 12 13 14] 
  Parameters: {'max_depth': 5, 'n_estimators': 100}
  Backtesting metric: 5563.729805331973



  0%|          | 1/2747 [00:02<2:15:13,  2.95s/it]

...

Number of models compared: 1


loop lags_grid: 100%|███████████████████████████████████████| 1/1 [00:01<00:00,  1.94s/it]


`Forecaster` refitted using the best-found lags and parameters, and the whole data set: 
  Lags: [ 1  2  3  4  5  6  7  8  9 10 11 12 13 14] 
  Parameters: {'max_depth': 5, 'n_estimators': 100}
  Backtesting metric: 0.013928391496838475



100%|██████████| 2747/2747 [00:00<00:00, 224232.78it/s]

TAMAÑO DE LOS DATOS:  2747 x 10


In [51]:
Proyecto.RMSE_Test_Promedio

1057.9197880649785